# Objective

This run will not have as much weight on winning, ultimately. It will focus on more iterations for the game in each round and set so that it can learn from a larger amount of data. 

In [1]:
from game import Game
from ai import SplendorAI
from player import get_phase_parameters
from constants import *
from datetime import datetime
# from player import get_phase_parameters
import sys
from collections import defaultdict
from collections import Counter



/usr/local/lib/python3.5/dist-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
# simply used to initialize players
base_game = Game(id=0, n_players=4)

In [3]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 6564523533082371597
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 9813544141
locality {
  bus_id: 1
  links {
  }
}
incarnation: 12746651013853063696
physical_device_desc: "device: 0, name: GeForce GTX 1080 Ti, pci bus id: 0000:01:00.0, compute capability: 6.1"
]


In [4]:
import tensorflow as tf
sess = tf.Session(config=tf.ConfigProto(log_device_placement=True))

In [5]:
# temperature will decrease over time
def calculate_temperature(round):
    return 1.8/(1 + round) /(1.5+round)

In [6]:
# constants to define; default
NETWORK_HYPERPARAMETERS = {
    # player input
    'player_funnel_layers': [15,12,10],
    'reserved_funnel_layers': [12,10,],
    'inject_reserved_at_player_funnel_index': 1, # 0 same as input, 1 = as first layer, etc.
    'card_funnel_layers': [12,12,8],
    # game input
    'game_funnel_layers': [15, 12, 10],
    'game_objective_funnel_layers': [10, 8],
    'game_card_funnel_layers': [15, 12, 10],
    # overall, slightly increased from default
    'main_dense_layers': [84, 36, 15], #this is when everything is combined

    # output layers
    # this does not include the win layer
    'output_layers': [
        {
            'name': 'Q1',
            'lag': 1,
            'score': 1,
            'discount': 0.1,
            'gems': 0.01,

        },
        {
            'name': 'Q3',
            'lag':  3,
            'score': 1,
            'discount': 0.1,
            'gems': 0,
        },
        {
            'name': 'Q5',
            'lag': 5,
            'score': 1,
            'discount': 0.05,
            'gems': 0,
        },
    ],
}

def get_phase_parameters(phase):
    """
    training will be divided into 5 phases

    """
    if phase==1:
        return {
            'Q1': 0.5,
            'Q3': 0.3,
            'Q5': 0.15,
            'win': 0.05,
        }
    elif phase==2:
        return {
            'Q1': 0.35,
            'Q3': 0.25,
            'Q5': 0.25,
            'win': 0.15,
        }
    elif phase==3:
        return {
            'Q1': 0.25,
            'Q3': 0.25,
            'Q5': 0.25,
            'win': 0.25,
        }
    elif phase==4:
        return {
            'Q1': 0.15,
            'Q3': 0.2,
            'Q5': 0.35,
            'win': 0.3,
        }
    elif phase==5:
        return {
            'Q1': 0.05,
            'Q3': 0.1,
            'Q5': 0.35,
            'win': 0.50,
        }
    elif phase==6:
        return {
            'Q1': 0.03,
            'Q3': 0.1,
            'Q5': 0.22,
            'win': 0.75
        }

In [7]:
players = base_game.players
game_data = defaultdict(list)



In [8]:
def summarize_counters(counter_list):
    master_counter = Counter()
    n = len(counter_list)
    for counter in counter_list:
        master_counter.update(counter)
    keys = list(master_counter.keys())
    for k in sorted(keys):
        master_counter[k] /= n
    return master_counter

In [9]:
set_durations = {}

# Test multiple runs of games

In [10]:
n_rounds = 6
n_sets_per_round = 3
n_simulations_per_set = 250

start_time = datetime.now()
for i in range(n_rounds):
    print('ON ROUND', i)
    for j in range(n_sets_per_round):
        set_start_time = datetime.now()
        for k in range(n_simulations_per_set):
            # if (i==0) and (j==0):
            #    # soft restart
            #    break
            new_game = Game(id=i*n_sets_per_round+n_simulations_per_set + j*n_simulations_per_set+k, 
                            players=players)
            stalemate = new_game.run()  
            # stalemates should be extraordinarily rare and pretty much nonexistent
            if stalemate: 
                very_long_game = new_game
                print('teaching ai not to stalemate')
                for player in players:
                    player.transfer_history_to_ai()
                    player.ai.train_models(verbose=0,n_epochs=3)
            sys.stdout.write('.')
            sys.stdout.flush()
            # record historic game data for each set
            game_data[(i,j)].append(new_game.copy_plain_data_for_self_and_players())
        set_stop_time = datetime.now()
        duration = (set_start_time-set_stop_time).seconds
        for player in players:
            player.transfer_history_to_ai()
            # train more epochs this time to make better predictions
            player.ai.train_models(verbose=0, n_epochs=30, batch_size=1500)
        set_durations[(i,j,k)] = duration
        print('/')
        sys.stdout.flush()
        avg_game_length = np.mean([x['game']['turn'] for x in game_data[(i,j)]])
        print('R/S %d/%d AVERAGE GAME LENGTH: ' % (i, j), avg_game_length)
        avg_cards_purchased = np.mean([
            [
                pdata['n_cards'] 
                for pdata in x['players'].values()
            ] 
            for x in game_data[(i,j)]
        ]
        )
        print('R/S %d/%d AVERAGE CARDS PURCHASED: ' % (i, j), avg_cards_purchased)
        # calculate win rates
        player_data = [x['players'] for x in game_data[(i,j)]]
        win_values = [[player_data[idx][pid]['win'] for idx in range(n_simulations_per_set)] for pid in range(4)]
        win_rates = [np.mean(v) for v in win_values]
        print('WIN RATES: ', str(win_rates))
        # reservation averages
        reservation_counters = [
            [
                player_data[idx][pid]['total_times_reserved'] 
                for idx in range(n_simulations_per_set)
            ]
            for pid in range(4)
        ]
        print('RESERVATION SUMMARY: ', [summarize_counters(counters) for counters in reservation_counters])
        
        # gem taking averages
        gem_counters = [
            [
                player_data[idx][pid]['total_gems_taken'] 
                for idx in range(n_simulations_per_set)
            ]
            for pid in range(4)
        ]
        print('GEMS SUMMARY: ', [summarize_counters(counters) for counters in gem_counters])
                             
    for player in players:
        player.reset(reset_extended_history=True)
    phase = min(3, i // 2 + 1)
    temperature = calculate_temperature(i)
    
    for p_i, player in enumerate(players):
        player.temperature = temperature
        player.decision_weighting = get_phase_parameters(phase)
        model_name = 'run7_player_%s_' % str(p_i)
        player.ai.save_models(model_name, index=i)
    
    
stop_time = datetime.now()
for time in [start_time, stop_time]:
    print(time.strftime('%x %X'))
    
# save historic data
import pickle
with open('run_7_game_data.dat', 'wb') as f:
    pickle.dump(game_data, f)
    
with open('run_7_duration_data.dat', 'wb') as f:
    pickle.dump(set_durations, f)
    


ON ROUND 0
........................................................................................................................................................................................................................................................../
R/S 0/0 AVERAGE GAME LENGTH:  147.72
R/S 0/0 AVERAGE CARDS PURCHASED:  13.534
WIN RATES:  [0.26, 0.236, 0.252, 0.256]
RESERVATION SUMMARY:  [Counter({(2, 'board'): 1.304, (3, 'board'): 1.212, (1, 'board'): 1.08, (2, 'topdeck'): 0.348, (3, 'topdeck'): 0.344, (1, 'topdeck'): 0.3}), Counter({(2, 'board'): 1.332, (3, 'board'): 1.236, (1, 'board'): 1.1, (2, 'topdeck'): 0.396, (3, 'topdeck'): 0.308, (1, 'topdeck'): 0.256}), Counter({(3, 'board'): 1.28, (2, 'board'): 1.256, (1, 'board'): 1.008, (3, 'topdeck'): 0.372, (2, 'topdeck'): 0.372, (1, 'topdeck'): 0.288}), Counter({(2, 'board'): 1.352, (3, 'board'): 1.336, (1, 'board'): 1.228, (3, 'topdeck'): 0.276, (2, 'topdeck'): 0.26, (1, 'topdeck'): 0.232})]
GEMS SUMMARY:  [Counter({3: 7.5

........................................................................................................................................................................................................................................................../
R/S 2/1 AVERAGE GAME LENGTH:  121.064
R/S 2/1 AVERAGE CARDS PURCHASED:  13.572
WIN RATES:  [0.228, 0.168, 0.26, 0.348]
RESERVATION SUMMARY:  [Counter({(3, 'board'): 1.312, (2, 'board'): 1.164, (1, 'board'): 1.06, (3, 'topdeck'): 0.296, (2, 'topdeck'): 0.284, (1, 'topdeck'): 0.256}), Counter({(3, 'board'): 1.296, (2, 'board'): 1.236, (1, 'board'): 1.004, (1, 'topdeck'): 0.276, (3, 'topdeck'): 0.244, (2, 'topdeck'): 0.232}), Counter({(3, 'board'): 1.264, (1, 'board'): 1.124, (2, 'board'): 1.116, (3, 'topdeck'): 0.292, (2, 'topdeck'): 0.276, (1, 'topdeck'): 0.248}), Counter({(3, 'board'): 1.2, (2, 'board'): 1.132, (1, 'board'): 1.12, (3, 'topdeck'): 0.312, (2, 'topdeck'): 0.276, (1, 'topdeck'): 0.268})]
GEMS SUMMARY:  [Counter({3: 7.852, 2: 

........................................................................................................................................................................................................................................................../
R/S 4/2 AVERAGE GAME LENGTH:  119.784
R/S 4/2 AVERAGE CARDS PURCHASED:  13.99
WIN RATES:  [0.2, 0.264, 0.24, 0.3]
RESERVATION SUMMARY:  [Counter({(3, 'board'): 1.848, (2, 'board'): 1.264, (1, 'board'): 0.876, (2, 'topdeck'): 0.232, (3, 'topdeck'): 0.144, (1, 'topdeck'): 0.128}), Counter({(3, 'board'): 1.996, (2, 'board'): 0.88, (1, 'board'): 0.716, (3, 'topdeck'): 0.172, (1, 'topdeck'): 0.148, (2, 'topdeck'): 0.1}), Counter({(3, 'board'): 1.552, (2, 'board'): 1.052, (1, 'board'): 1.048, (2, 'topdeck'): 0.22, (3, 'topdeck'): 0.216, (1, 'topdeck'): 0.16}), Counter({(3, 'board'): 1.44, (2, 'board'): 1.156, (1, 'board'): 1.032, (2, 'topdeck'): 0.22, (3, 'topdeck'): 0.216, (1, 'topdeck'): 0.2})]
GEMS SUMMARY:  [Counter({3: 8.12, 2: 3.008, 0: 0

In [11]:
player_data

[{0: {'cards': [{'color': 'green', 'cost': ColorCombination object: 
     {
         "white": 2,
         "red": 0,
         "blue": 1,
         "black": 0,
         "green": 0
     }, 'cost_': {'black': 0,
      'blue': 1,
      'green': 0,
      'red': 0,
      'white': 2}, 'points': 0, 'tier': 1},
    {'color': 'black', 'cost': ColorCombination object: 
     {
         "white": 1,
         "red": 1,
         "blue": 1,
         "black": 0,
         "green": 1
     }, 'cost_': {'black': 0,
      'blue': 1,
      'green': 1,
      'red': 1,
      'white': 1}, 'points': 0, 'tier': 1},
    {'color': 'black', 'cost': ColorCombination object: 
     {
         "white": 3,
         "red": 0,
         "blue": 2,
         "black": 0,
         "green": 2
     }, 'cost_': {'black': 0,
      'blue': 2,
      'green': 2,
      'red': 0,
      'white': 3}, 'points': 1, 'tier': 2},
    {'color': 'green', 'cost': ColorCombination object: 
     {
         "white": 0,
         "red": 0,
         "blue

In [12]:
# players[0].ai.load_models('run6_player_0_round_', 1)

In [13]:
from collections import Mapping, Container 
from sys import getsizeof

def deep_getsizeof(o, ids): 

    d = deep_getsizeof
    if id(o) in ids:
        return 0

    r = getsizeof(o)
    ids.add(id(o))

    if isinstance(o, str) or isinstance(0, bytes):
        return r
    
    if isinstance(o, np.ndarray):
        return r

    if isinstance(o, Mapping):
        return r + sum(d(k, ids) + d(v, ids) for k, v in o.items())

    if isinstance(o, Container):
        return r + sum(d(x, ids) for x in o)

    return r

deep_getsizeof(game_data, set())
# deep_getsizeof(players[0].extended_serialized_action_history[0], set())

# for k in list(locals().keys()):
#    v = locals()[k]
#    size = deep_getsizeof(v, set())
#    if size > 100000:
#        print(k, ':', size)

273803027

In [14]:
# players[1].reset(reset_extended_history=True)
# for k in dir(players[1]):
#    v = getattr(players[1], k)
#    if isinstance(v, (list, dict)):
#        print(k, len(v))

In [15]:
#new_game = Game(id=i*200 + j*100+1.1, players=players)

In [16]:
#for k in dir(players[2]):
#    v = getattr(players[2], k)
#    if isinstance(v, (list, dict)):
#        print(k, len(v))

In [17]:
#len(players[0].ai.extended_serialized_history)

# NOTES

Runs are complete. Data can be analyzed in a different environment. Tweaks may be made for future runs based on simulation results from loaded models.